In [3]:
import pandas as pd
import numpy as np

In [4]:
df = pd.read_csv('news.csv', delimiter =',')

In [5]:
df.drop(["Unnamed: 0",'publish_date','url'], axis = 1, inplace = True)

In [6]:
df['authors'] = df['authors'].str.strip('[]')
df['authors'] = df['authors'].str.strip('  ''')
df['authors'] = df.authors.str.replace("[({':]", "")
df['authors'] = df['authors'].str.lower()

In [7]:
import re

df['authors'].replace(to_replace = [r'cbcs?\b.*',r'.*\bcbcs?', r'.*cbcnews.*'], value='cbc', regex=True, inplace=True)
df['authors'].replace(to_replace = ['the associated press'], value='associated press', inplace=True)
df['authors'].replace(to_replace = [r'canadian?\b.*',r'.*\bcanadian?'], value='canadian', regex=True, inplace=True)
df['authors'].replace(to_replace = [r'freelancer?\b.*',r'.*\bfreelancer?'], value='freelancer', regex=True, inplace=True)

In [8]:
import string
string.punctuation

'!"#$%&\'()*+,-./:;<=>?@[\\]^_`{|}~'

In [9]:
def remove_punct(text):
    text_nopunct = "".join([char for char in text if char not in string.punctuation])
    return text_nopunct

In [10]:
df['body_text_clean'] = df['text'].apply(lambda x: remove_punct(x))

In [11]:
def tokenize(text):
    tokens = re.split('\W+', text)
    return tokens

In [12]:
df['body_text_tokenized'] = df['body_text_clean'].apply(lambda x: tokenize(x.lower()))

In [ ]:
#N-grams

In [ ]:
import re
import math
import numpy as np
from itertools import chain
from collections import Counter
import nltk
from nltk.util import ngrams # This is the ngram magic.
from textblob import TextBlob

In [ ]:
NGRAM = 4

In [ ]:
def get_tuples_nosentences(txt):
    """Get tuples that ignores all punctuation (including sentences)."""
    if not txt: return None
    ng = ngrams(re_stripper_alpha.sub(' ', txt).split(), NGRAM)
    return list(ng)

In [ ]:
def get_tuples_textblob_sentences(txt):
    """New get_tuples that does use textblob."""
    if not txt: return None
    tb = TextBlob(txt)
    ng = (ngrams(x.words, NGRAM) for x in tb.sentences if len(x.words) > NGRAM)
    return [item for sublist in ng for item in sublist]

In [ ]:
paragraph= """Canadian pharmacies are limiting how much medi.
The Jewish General Hospital plan"""

In [ ]:
arr1 = get_tuples_textblob_sentences(paragraph);

In [ ]:
print("Number of N-grams:", len(arr1));arr1

In [ ]:
#accard similarity coefficient score

"""The Jaccard index [1], or Jaccard similarity coefficient, defined as the size of the 
intersection divided by the size of the union of two label sets, 
is used to compare set of predicted labels for a sample to the corresponding set of labels in y_true."""


def jaccard_distance(a, b):
    """Calculate the jaccard distance between sets A and B"""
    a = set(a)
    b = set(b)
    return 1.0 * len(a&b)/len(a|b)

In [ ]:
def cosine_similarity_ngrams(a, b):
    vec1 = Counter(a)
    vec2 = Counter(b)
    
    intersection = set(vec1.keys()) & set(vec2.keys())
    numerator = sum([vec1[x] * vec2[x] for x in intersection])

    sum1 = sum([vec1[x]**2 for x in vec1.keys()])
    sum2 = sum([vec2[x]**2 for x in vec2.keys()])
    denominator = math.sqrt(sum1) * math.sqrt(sum2)
    
   
    if not denominator:
        return 0.0
    return float(numerator) / denominator

In [ ]:
a = get_tuples_nosentences("The quick brown fox jumps.")
arr1 = get_tuples_textblob_sentences("The quick brown fox jumps.");
print(arr1);

b = get_tuples_nosentences("The quick brown fox wont jumps.")
arr2 = get_tuples_textblob_sentences("The quick brown fox wont jumps.");
print(arr2)

print("Jaccard: {}   Cosine: {}".format(jaccard_distance(a,b), cosine_similarity_ngrams(a,b)))

In [ ]:
a = get_tuples_nosentences("The quick brown dont want to jump.")
b = get_tuples_nosentences("The quick brown dont want to jump.")
print("Jaccard: {}   Cosine: {}".format(jaccard_distance(a,b), cosine_similarity_ngrams(a,b)))

In [ ]:
a = get_tuples_nosentences("Above is a bad example of four-gram similarity.")
b = get_tuples_nosentences("This is a better example of four-gram similarity.")
print("Jaccard: {}   Cosine: {}".format(jaccard_distance(a,b), cosine_similarity_ngrams(a,b)))

In [13]:
import nltk

In [14]:
stopword = nltk.corpus.stopwords.words('english')

In [15]:
def remove_stopwords(tokenized_list):
    text = [word for word in tokenized_list if word not in stopword]
    return text

In [16]:
df['body_text_nostop'] = df['body_text_tokenized'].apply(lambda x: remove_stopwords(x))

In [17]:
ps=nltk.PorterStemmer()

In [18]:
def stemming(tokenized_text):
    text = [ps.stem(word) for word in tokenized_text]
    return text

In [19]:
df['body_text_stemmed'] = df['body_text_nostop'].apply(lambda x: stemming(x))


In [20]:
wn=nltk.WordNetLemmatizer()

In [21]:
def lemmatizing(tokenized_text):
    text = [wn.lemmatize(word) for word in tokenized_text]
    return text

In [22]:
df['body_text_lemmatized'] = df['body_text_nostop'].apply(lambda x: lemmatizing(x))


In [22]:
#Import all the dependencies
from gensim.models.doc2vec import Doc2Vec, TaggedDocument
from nltk.tokenize import word_tokenize

In [2]:
import multiprocessing

In [ ]:
word_vectors = w2v.wv #get trained embeddings - an KeyedVector instance


In [ ]:
EMB_DIM = 300
w2v = Word2Vec(sentences,size=EMB_DIM,window=5,min_count=5,negative=15,iter=10,workers=multiprocessing.cpu_count())

In [25]:
from nltk.corpus import conll2000

In [31]:
import tensorflow as tf

In [26]:
train_words=conll2000.tagged_words("train.txt")

In [27]:
test_words=conll2000.tagged_words("test.txt")

In [28]:
print(train_words[:10])

[('Confidence', 'NN'), ('in', 'IN'), ('the', 'DT'), ('pound', 'NN'), ('is', 'VBZ'), ('widely', 'RB'), ('expected', 'VBN'), ('to', 'TO'), ('take', 'VB'), ('another', 'DT')]


In [1]:
def get_tag_vocabulary(tagged_words):
    tag2id = {}
    for item in tagged_words:
        tag = item[1]
        tag2id.setdefault(tag, len(tag2id))
    return tag2id

word2id = {k:v.index for k,v in word_vectors.vocab.items()}
tag2id = get_tag_vocabulary(train_words)

NameError: name 'word_vectors' is not defined

In [ ]:
def get_int_data(tagged_words,wordid,tagid):
    X,Y = [],[]
    unk_count=0 #to keep track of unknown words
    
    for word,tag in tagged_words:
        Y.append(tagid.get(tag))
        if word in word2id:
            X.append(word2id.get(word))
        else:
            X.append(UNK_INDEX)
            unk_count+=1
    print("%.3f" %(unk_count/len(tagged_data)))
    return np.array(X), np.array(Y)
X_train,Y_train = get_int_data(train_words,word2id,tag2id)
X_test,Y_test = get_int_data(test_words,word2id,tag2id)

Y_train,Y_test = to_categorical(Y_train),to_categorical(Y_test)

In [ ]:
def add_new_word(new_word,new_vector,new_index,embedding_matrix,word2id):
    embedding_matrix = np.insert(embedding_matrix,[new_index],[new_vector],axis=0)
    word2id = {word:(index +1) if index >=new_index else index
              for word,index in word2id.items()}
    word2id[new_word]=new_index
    return embedding_matrix,word2id

UNK_INDEX = 0
UNK_TOKEN = "UNK"

embedding_matrix = word_vectors.vectors
unk_vector=embedding_matrix.mean(0)
embedding_matrix,word2id = add_new_word(UNK_TOKEN,unk_vector,UNK_INDEX,embedding_matrix,word2id)

In [ ]:
HIDDEN_SIZE = 50
BATCH_SIZE =128

def define_model(embedding_matrix,class_count):
    vocab_length=len(embedding_matrix)
    model = tf.keras.models.Sequential()
    
    model.add(Embedding(input_dim=vocab_length,
                       output_dim=EMB_DIM, #output of this layer is the embedding of the input word
                       weights=[embedding_matrix], #the matrix holding the trained embeddings
                       input_length=1))#specifies how many indexes we are looking up
    model.add(Flatten())
    model.add(Dense(HIDDEN_SIZE))
    model.add(Activation("tanh"))
    model.add(Dense(class_count))
    model.add(Activation("softmax"))
    
    model.compile(optimizer=tf.optimizers.Adam(),
                  loss="categorical_crossentropy",
                  metrics = ["accuracy"])
    return model

pos_model = define_model(embedding_matrix,len(tag2id))
pos_model.summary()

pos_model.fit(X_train,
             Y_train,
             batch_size=BATCH_SIZE,
             epochs=0,
             verbose=1)

In [ ]:
def evaluate_model(model,id2word,x_test,y_test):
    """Prints most mistagged words"""
    _, acc= model.evaluate(x_test,y_test)#get accuaracy of the model
    print("Accuracy: %.2f" %acc)
    
    y_pred = model.predict_classes(x_test) # get model predictions
    error_counter = collections.Counter() # to count model errors
    
    for i in range(len(x_test)):
        correct_tag_id=np.argmax(x_test[i])
        if y_pred[i] != correct_tag_id:
            word = id2word[x_test[i]]
            error_counter[word] +=1
    print("Most common errors:\n",error_counter.most_common(5))
    
id2word = sorted(word2id,key=word2id.get)

In [ ]:
EOS_INDEX=1
EOS_TOKEN="EOS"

#Creating a random end-of-sequence vector
eos_vector = np.random.standard_normal(EMB_DIM)
embedding_matrix, word2id=add_new_word(EOS_TOKEN,eos_vector,EOS_INDEX,embedding_matrix,word2id)


In [ ]:
CONTEXT_SIZE=2

def get_window_int_data(tagged_words,word2id,tag2id):
    X,Y=[],[]
    unk_count=0
    
    span=2*CONTEXT_SIZE +1 
    buffer = collections.deque(maxlen=span)
    padding = [(EOS_TOKEN,None)] * CONTEXT_SIZE
    buffer += padding + train_words[:CONTEXT_SIZE]
    
    for item in (train_words[CONTEXT_SIZE:] + padding):
        
        window_ids = np.array([word2id.get(word) if (word in word2id) else UNK_INDEX
                              for (word, _) in buffer ])
        X.append(window_ids)
        
        #the label is the tag of the middle word
        middle_word,middle_tag=buffer[CONTEXT_SIZE]
        Y.append(tag2id.get(middle_tag))
        
        if middle_word not in word2id:
            unk_count +=1
    print("Data Created. Percentage of unknown words: %.3f" %(unk_count/len(tagged_words)))
    return np.array(X),np.array(Y)



In [ ]:
def define_context_sensitive_model(embedding_matrix,class_count):
    vocab_length=len(embedding_matrix)
    total_span = CONTEXT_SIZE * 2 +1
    model = tf.keras.models.Sequential()
    
    model.add(Embedding(input_dim=vocab_length,
                       output_dim=EMB_DIM, #output of this layer is the embedding of the input word
                       weights=[embedding_matrix], #the matrix holding the trained embeddings
                       input_length=total_span)),#specifies how many indexes we are looking up
    model.add(Flatten())
    model.add(Dense(HIDDEN_SIZE))
    model.add(Activation("tanh"))
    model.add(Dense(class_count))
    model.add(Activation("softmax"))
    
    model.compile(optimizer=tf.optimizers.Adam(),
                  loss="categorical_crossentropy",
                  metrics = ["accuracy"])
    return model

In [ ]:
X_train2,Y_train2=get_window_int_data(train_words,word2id,tag2id)
X_test2,Y_test2=get_window_int_data(test_words,word2id,tag2id)
Y_train2,Y_test2 = to_categorical(Y_train2),to_categorical(Y_test2)

cs_pos_model = define_model(embedding_matrix,len(tag2id))
cs_pos_model.summary()

cs_pos_model.fit(X_train2,
                  Y_train2,
                  batch_size=BATCH_SIZE,
                  epochs=0,
                  verbose=1)

In [12]:
import numpy as np
from collections import defaultdict

In [33]:
class word2vec():

	def __init__(self):
		self.n = settings['n']
		self.lr = settings['learning_rate']
		self.epochs = settings['epochs']
		self.window = settings['window_size']

	def generate_training_data(self, settings, corpus):
		# Find unique word counts using dictonary
		word_counts = defaultdict(int)
		for row in corpus:
			for word in row:
				word_counts[word] += 1
		#########################################################################################################################################################
		print(word_counts)																																	#
		# # defaultdict(<class 'int'>, {'natural': 1, 'language': 1, 'processing': 1, 'and': 2, 'machine': 1, 'learning': 1, 'is': 1, 'fun': 1, 'exciting': 1})	#
		#########################################################################################################################################################

		## How many unique words in vocab? 9
		self.v_count = len(word_counts.keys())
		#########################
		print(self.v_count)	#
		# 9						#
		#########################

		# Generate Lookup Dictionaries (vocab)
		self.words_list = list(word_counts.keys())
		#################################################################################################
		print(self.words_list)																		#
		# ['natural', 'language', 'processing', 'and', 'machine', 'learning', 'is', 'fun', 'exciting']	#
		#################################################################################################
		
		# Generate word:index
		self.word_index = dict((word, i) for i, word in enumerate(self.words_list))
		#############################################################################################################################
		print(self.word_index)																									#
		# # {'natural': 0, 'language': 1, 'processing': 2, 'and': 3, 'machine': 4, 'learning': 5, 'is': 6, 'fun': 7, 'exciting': 8}	#
		#############################################################################################################################

		# Generate index:word
		self.index_word = dict((i, word) for i, word in enumerate(self.words_list))
		#############################################################################################################################
		print(self.index_word)																									#
		# {0: 'natural', 1: 'language', 2: 'processing', 3: 'and', 4: 'machine', 5: 'learning', 6: 'is', 7: 'fun', 8: 'exciting'}	#
		#############################################################################################################################

		training_data = []

		# Cycle through each sentence in corpus
		for sentence in corpus:
			sent_len = len(sentence)

			# Cycle through each word in sentence
			for i, word in enumerate(sentence):
				# Convert target word to one-hot
				w_target = self.word2onehot(sentence[i])

				# Cycle through context window
				w_context = []

				# Note: window_size 2 will have range of 5 values
				for j in range(i - self.window, i + self.window+1):
					# Criteria for context word 
					# 1. Target word cannot be context word (j != i)
					# 2. Index must be greater or equal than 0 (j >= 0) - if not list index out of range
					# 3. Index must be less or equal than length of sentence (j <= sent_len-1) - if not list index out of range 
					if j != i and j <= sent_len-1 and j >= 0:
						# Append the one-hot representation of word to w_context
						w_context.append(self.word2onehot(sentence[j]))
						print(sentence[i], sentence[j]) 
						#########################
						# Example:				#
						# natural language		#
						# natural processing	#
						# language natural		#
						# language processing	#
						# language append 		#
						#########################
						
				# training_data contains a one-hot representation of the target word and context words
				#################################################################################################
				# Example:																						#
				# [Target] natural, [Context] language, [Context] processing									#
				print(training_data)																			#
				# [[[1, 0, 0, 0, 0, 0, 0, 0, 0], [[0, 1, 0, 0, 0, 0, 0, 0, 0], [0, 0, 1, 0, 0, 0, 0, 0, 0]]]]	#
				#################################################################################################
				training_data.append([w_target, w_context])

		return np.array(training_data)

	def word2onehot(self, word):
		# word_vec - initialise a blank vector
		word_vec = [0 for i in range(0, self.v_count)] # Alternative - np.zeros(self.v_count)
		#############################
		print(word_vec)			#
		# [0, 0, 0, 0, 0, 0, 0, 0]	#
		#############################

		# Get ID of word from word_index
		word_index = self.word_index[word]

		# Change value from 0 to 1 according to ID of the word
		word_vec[word_index] = 1

		return word_vec

	def train(self, training_data):
		# Initialising weight matrices
		# np.random.uniform(HIGH, LOW, OUTPUT_SHAPE)
		# https://docs.scipy.org/doc/numpy-1.15.1/reference/generated/numpy.random.uniform.html
		# self.w1 = np.array(getW1)
		# self.w2 = np.array(getW2)
		self.w1 = np.random.uniform(-1, 1, (self.v_count, self.n))
		self.w2 = np.random.uniform(-1, 1, (self.n, self.v_count))
		
		# Cycle through each epoch
		for i in range(self.epochs):
			# Intialise loss to 0
			self.loss = 0
			# Cycle through each training sample
			# w_t = vector for target word, w_c = vectors for context words
			for w_t, w_c in training_data:
				# Forward pass
				# 1. predicted y using softmax (y_pred) 2. matrix of hidden layer (h) 3. output layer before softmax (u)
				y_pred, h, u = self.forward_pass(w_t)
				#########################################
				print("Vector for target word:", w_t)	#
				print("W1-before backprop", self.w1)	#
				print("W2-before backprop", self.w2)	#
				#########################################

				# Calculate error
				# 1. For a target word, calculate difference between y_pred and each of the context words
				# 2. Sum up the differences using np.sum to give us the error for this particular target word
				EI = np.sum([np.subtract(y_pred, word) for word in w_c], axis=0)
				#########################
				print("Error", EI)	#
				#########################

				# Backpropagation
				# We use SGD to backpropagate errors - calculate loss on the output layer 
				self.backprop(EI, h, w_t)
				#########################################
				print("W1-after backprop", self.w1)	#
				print("W2-after backprop", self.w2)	#
				#########################################

				# Calculate loss
				# There are 2 parts to the loss function
				# Part 1: -ve sum of all the output +
				# Part 2: length of context words * log of sum for all elements (exponential-ed) in the output layer before softmax (u)
				# Note: word.index(1) returns the index in the context word vector with value 1
				# Note: u[word.index(1)] returns the value of the output layer before softmax
				self.loss += -np.sum([u[word.index(1)] for word in w_c]) + len(w_c) * np.log(np.sum(np.exp(u)))
				
				#############################################################
				# Break if you want to see weights after first target word 	#
				# break 													#
				#############################################################
			print('Epoch:', i, "Loss:", self.loss)

	def forward_pass(self, x):
		# x is one-hot vector for target word, shape - 9x1
		# Run through first matrix (w1) to get hidden layer - 10x9 dot 9x1 gives us 10x1
		h = np.dot(x, self.w1)
		# Dot product hidden layer with second matrix (w2) - 9x10 dot 10x1 gives us 9x1
		u = np.dot(h, self.w2)
		# Run 1x9 through softmax to force each element to range of [0, 1] - 1x8
		y_c = self.softmax(u)
		return y_c, h, u

	def softmax(self, x):
		e_x = np.exp(x - np.max(x))
		return e_x / e_x.sum(axis=0)

	def backprop(self, e, h, x):
		# https://docs.scipy.org/doc/numpy-1.15.1/reference/generated/numpy.outer.html
		# Column vector EI represents row-wise sum of prediction errors across each context word for the current center word
		# Going backwards, we need to take derivative of E with respect of w2
		# h - shape 10x1, e - shape 9x1, dl_dw2 - shape 10x9
		# x - shape 9x1, w2 - 10x9, e.T - 9x1
		dl_dw2 = np.outer(h, e)
		dl_dw1 = np.outer(x, np.dot(self.w2, e.T))
		########################################
		# print('Delta for w2', dl_dw2)			#
		# print('Hidden layer', h)				#
		# print('np.dot', np.dot(self.w2, e.T))	#
		# print('Delta for w1', dl_dw1)			#
		#########################################

		# Update weights
		self.w1 = self.w1 - (self.lr * dl_dw1)
		self.w2 = self.w2 - (self.lr * dl_dw2)

	# Get vector from word
	def word_vec(self, word):
		w_index = self.word_index[word]
		v_w = self.w1[w_index]
		return v_w

	# Input vector, returns nearest word(s)
	def vec_sim(self, word, top_n):
		v_w1 = self.word_vec(word)
		word_sim = {}

		for i in range(self.v_count):
			# Find the similary score for each word in vocab
			v_w2 = self.w1[i]
			theta_sum = np.dot(v_w1, v_w2)
			theta_den = np.linalg.norm(v_w1) * np.linalg.norm(v_w2)
			theta = theta_sum / theta_den

			word = self.index_word[i]
			word_sim[word] = theta

		words_sorted = sorted(word_sim.items(), key=lambda kv: kv[1], reverse=True)

		for word, sim in words_sorted[:top_n]:
			print(word, sim)

In [34]:
settings = {
	'window_size': 2,			# context window +- center word
	'n': 10,					# dimensions of word embeddings, also refer to size of hidden layer
	'epochs': 50,				# number of training epochs
	'learning_rate': 0.01		# learning rate
}

In [35]:
text = "Canadian pharmacies are limiting how much mediThe Yukon government has identified two places The Senate late Wednesday passed an unparallel"

In [36]:
corpus = [[word.lower() for word in text.split()]]

In [37]:
# Initialise object
w2v = word2vec()

In [38]:
# Numpy ndarray with one-hot representation for [target_word, context_words]
training_data = w2v.generate_training_data(settings, corpus)

defaultdict(<class 'int'>, {'canadian': 1, 'pharmacies': 1, 'are': 1, 'limiting': 1, 'how': 1, 'much': 1, 'medithe': 1, 'yukon': 1, 'government': 1, 'has': 1, 'identified': 1, 'two': 1, 'places': 1, 'the': 1, 'senate': 1, 'late': 1, 'wednesday': 1, 'passed': 1, 'an': 1, 'unparallel': 1})
20
['canadian', 'pharmacies', 'are', 'limiting', 'how', 'much', 'medithe', 'yukon', 'government', 'has', 'identified', 'two', 'places', 'the', 'senate', 'late', 'wednesday', 'passed', 'an', 'unparallel']
{'canadian': 0, 'pharmacies': 1, 'are': 2, 'limiting': 3, 'how': 4, 'much': 5, 'medithe': 6, 'yukon': 7, 'government': 8, 'has': 9, 'identified': 10, 'two': 11, 'places': 12, 'the': 13, 'senate': 14, 'late': 15, 'wednesday': 16, 'passed': 17, 'an': 18, 'unparallel': 19}
{0: 'canadian', 1: 'pharmacies', 2: 'are', 3: 'limiting', 4: 'how', 5: 'much', 6: 'medithe', 7: 'yukon', 8: 'government', 9: 'has', 10: 'identified', 11: 'two', 12: 'places', 13: 'the', 14: 'senate', 15: 'late', 16: 'wednesday', 17: 'pa

In [39]:
# Training
w2v.train(training_data)

Vector for target word: [1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
W1-before backprop [[-0.81209503  0.42589427  0.3427108  -0.7454827  -0.44547233 -0.05184684
   0.8842167   0.41780753  0.60552354  0.51724073]
 [ 0.38102792  0.71703803  0.38188631 -0.23734518 -0.20511986  0.91315174
   0.17190975 -0.90421418  0.50741469  0.34002686]
 [ 0.59700114 -0.06005414  0.49360559  0.35893557  0.1567104   0.77438917
   0.79421883 -0.35833802  0.17053784  0.64208058]
 [-0.03515376  0.22104485  0.86110324  0.44611824 -0.16722381 -0.61722339
  -0.78346786  0.2562353  -0.05486292  0.72205443]
 [-0.0619006  -0.27548144 -0.57551005 -0.12298276  0.10480322 -0.17957263
  -0.2960918  -0.07311391 -0.32800123  0.8877932 ]
 [ 0.79268509  0.26061955 -0.34438036  0.39402307 -0.556422   -0.5628302
   0.72296626 -0.91815857 -0.47511547 -0.05154788]
 [-0.51330919  0.23924239  0.3550446  -0.90765116  0.16291114 -0.67248624
  -0.60720207  0.54895051  0.86823533  0.19895774]
 [ 0.92504817 -0.40656

  -4.47064738e-01  8.77490242e-01]]
W2-before backprop [[-0.34901961 -0.82892541 -0.00747879  0.42295998 -0.85217283 -0.48849317
  -0.31759755 -0.00874087  0.82761169 -0.83090998 -0.17354496  0.7555615
   0.84125873 -0.10791313  0.96113681 -0.64569985  0.88973588 -0.90768667
  -0.71674874  0.60176467]
 [-0.9614193  -0.51995888 -0.78546108  0.2670514   0.20038009  0.28000688
  -0.89973548 -0.07325262  0.26920473  0.98119529 -0.84710666  0.5943709
   0.48410423  0.46838558 -0.00895873 -0.86913945  0.64387138  0.04630757
  -0.58629775 -0.76400361]
 [-0.34980067 -0.60611481 -0.88729082  0.2180798   0.16141081 -0.36597877
   0.77938856 -0.77208277 -0.14410097 -0.90356523 -0.43289772  0.5889088
   0.47901679  0.62682361  0.03847791 -0.9756897   0.84749775 -0.55817995
   0.41386023 -0.51945826]
 [-0.21969948 -0.34153047  0.15941484 -0.50952227  0.12163698  0.36759803
   0.30696468  0.87149145  0.8813088  -0.68298724  0.4974654  -0.27125368
  -0.45424489 -0.32240264 -0.13368102  0.92595786 -0.

   0.86563962 -0.03805159]]
Vector for target word: [0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
W1-before backprop [[-0.83316226  0.38135772  0.2977622  -0.73546179 -0.41227898 -0.05084459
   0.84894081  0.4414879   0.62703169  0.5192432 ]
 [ 0.35556937  0.65477013  0.33689385 -0.24517414 -0.22209606  0.89634716
   0.13120089 -0.89354373  0.53276185  0.34558747]
 [ 0.52172344 -0.08488591  0.47021992  0.32406925  0.15504784  0.72529361
   0.74382491 -0.31119477  0.20769047  0.66547749]
 [-0.1069088   0.20478903  0.77722015  0.46345276 -0.11945329 -0.58109761
  -0.79731686  0.28929072 -0.01364675  0.68837569]
 [-0.05920728 -0.26926632 -0.5601553  -0.11014247  0.05373246 -0.15811174
  -0.33904358 -0.05177895 -0.31394286  0.86857858]
 [ 0.76047339  0.25792373 -0.32440933  0.40587677 -0.55274902 -0.5545337
   0.66631602 -0.89596742 -0.46083748 -0.03881885]
 [-0.50989923  0.24859555  0.33829164 -0.84176072  0.16541585 -0.62488299
  -0.59941948  0.53065558  0.8371223   0.1815

  -4.39420654e-01  8.63251573e-01]]
W2-before backprop [[-0.32758567 -0.82474015 -0.06576517  0.46524229 -0.82332493 -0.48400418
  -0.29155144 -0.02920996  0.81607234 -0.83550523 -0.19010127  0.75288663
   0.79875772 -0.08881432  0.93448518 -0.64771082  0.90035844 -0.90161736
  -0.69854947  0.60577507]
 [-0.93906581 -0.50948405 -0.75022199  0.26595877  0.18620542  0.26101493
  -0.90324824 -0.07083191  0.24550293  0.99116108 -0.83798128  0.54668106
   0.52391742  0.46564942 -0.00283698 -0.84479662  0.62538001  0.01540691
  -0.59116928 -0.75769729]
 [-0.33252074 -0.56308123 -0.83015871  0.20865384  0.19518892 -0.35604656
   0.73235351 -0.78478022 -0.14286529 -0.90268112 -0.47721615  0.549019
   0.4393314   0.58414935  0.050257   -0.95768477  0.82181134 -0.52109976
   0.4160732  -0.49039842]
 [-0.22126924 -0.32436353  0.13839896 -0.51083047  0.12485876  0.33767698
   0.30526132  0.83901053  0.81371058 -0.66378486  0.49749398 -0.27816695
  -0.43431165 -0.28811451 -0.11098671  0.95541498 -0

   0.85333986 -0.59117019 -0.43546023  0.85639315]]
W2-after backprop [[-3.20192297e-01 -8.25560950e-01 -9.28827786e-02  4.82062591e-01
  -8.12671944e-01 -4.82190078e-01 -2.79832665e-01 -3.76489959e-02
   8.10958842e-01 -8.37580044e-01 -1.96647942e-01  7.53324225e-01
   7.81224367e-01 -7.91067999e-02  9.22753501e-01 -6.48237431e-01
   9.07061720e-01 -8.98792195e-01 -6.89149757e-01  6.08206325e-01]
 [-9.27595122e-01 -5.04513198e-01 -7.37795483e-01  2.64286451e-01
   1.79343632e-01  2.48403798e-01 -9.05918965e-01 -6.92793391e-02
   2.35102776e-01  9.96338729e-01 -8.32887843e-01  5.26652245e-01
   5.44721617e-01  4.64974168e-01  8.12142025e-04 -8.32725305e-01
   6.17425340e-01  3.07652074e-04 -5.93502400e-01 -7.54606403e-01]
 [-3.24078929e-01 -5.45868017e-01 -8.12813140e-01  2.01053470e-01
   2.06402677e-01 -3.59655077e-01  7.09016680e-01 -7.88323656e-01
  -1.40556405e-01 -9.01030884e-01 -4.96470642e-01  5.32971999e-01
   4.23767377e-01  5.65909082e-01  5.82180868e-02 -9.47344563e-01
   8

...

   1.98236745e-01 -6.39390878e-01  6.18968619e-01  5.75832359e-04]]
Vector for target word: [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0]
W1-before backprop [[-1.06096256e+00  6.75604706e-02  5.50118516e-03 -6.92270629e-01
  -1.73617006e-01 -6.78826006e-02  4.31425872e-01  6.69796831e-01
   8.67699360e-01  6.77724057e-01]
 [ 1.57978204e-01  1.59276998e-01  5.27561918e-02 -4.33611874e-01
  -4.26255288e-01  8.24850588e-01 -1.49712805e-01 -9.50095176e-01
   8.35701300e-01  6.20301565e-01]
 [-1.06557549e-02 -2.10891705e-01  3.86209578e-01 -1.44898121e-02
   1.56771614e-01  2.92050025e-01  3.95027574e-01 -1.27210375e-01
   5.55698756e-01  1.07650772e+00]
 [-7.86446798e-01  9.16845991e-02  3.64721510e-01  4.23545048e-01
   1.37485923e-01 -4.43192708e-01 -1.00833832e+00  5.62030098e-01
   3.63965306e-01  6.40621597e-01]
 [-7.74184723e-02 -3.49548081e-01 -3.94974121e-01 -1.14667353e-01
  -6.39008106e-01  5.19084992e-02 -9.99254278e-01 -2.40912115e-02
  -2.43058824e-01  8.0773851

  -2.68312161e-01  6.50150871e-01]]
W2-after backprop [[-2.72072631e-01 -1.00778785e+00 -7.71537234e-01  7.32058197e-01
  -6.93750136e-01 -5.85725114e-01 -6.93758557e-02 -1.93009766e-01
   6.75498736e-01 -9.00107460e-01 -2.82559645e-01  9.79156633e-01
   6.00682155e-01  2.50847333e-01  6.92951968e-01 -5.34103427e-01
   1.19431502e+00 -8.55546577e-01 -5.76592527e-01  6.81755873e-01]
 [-7.45182352e-01 -5.30100114e-01 -6.05465919e-01  1.58237350e-01
   4.59854801e-02 -1.96871069e-02 -8.84007952e-01 -8.15179648e-02
   1.49401260e-01  1.14459501e+00 -6.38701537e-01  3.38736673e-01
   1.22825317e+00  5.10329439e-01  1.60943209e-01 -5.92500852e-01
   4.67391188e-01 -4.72831638e-01 -8.51889812e-01 -8.62443037e-01]
 [-1.82565145e-01 -2.72776922e-01 -5.48636923e-01  2.12050975e-01
   4.30977978e-01 -3.48307282e-01  2.81838188e-01 -1.02642542e+00
  -1.38174282e-01 -9.01058761e-01 -1.18223447e+00  1.95955914e-01
   8.66004970e-02  3.22511211e-01  3.31888966e-01 -7.04218786e-01
   8.11541554e-01 -3

   1.81714390e-01 -6.40651755e-01  6.10096472e-01  5.54146062e-04]]
Vector for target word: [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0]
W1-before backprop [[-1.07169933  0.05931798 -0.00404707 -0.69309897 -0.16890675 -0.06770853
   0.41109033  0.67826484  0.87798145  0.68770849]
 [ 0.1484483   0.14436549  0.04459646 -0.44512572 -0.43591577  0.82541968
  -0.16041306 -0.95516551  0.85015159  0.6392536 ]
 [-0.0260637  -0.20959901  0.38836761 -0.02772675  0.15588472  0.27371154
   0.37916139 -0.12969162  0.56702758  1.09920262]
 [-0.81031915  0.08892306  0.35848851  0.41516103  0.13982213 -0.44411399
  -1.0205739   0.56919227  0.37514037  0.64448291]
 [-0.0820903  -0.3570068  -0.39070912 -0.12069802 -0.66207557  0.05901359
  -1.02575424 -0.02900253 -0.24100309  0.81361503]
 [ 0.43300903  0.14281791 -0.00777058  0.61261024 -0.4401997  -0.4708204
  -0.14583849 -0.872491   -0.3271245   0.29225865]
 [-0.41732813  0.37206891  0.08654522 -0.04602564  0.15716973 -0.22796662
  -0.

  -2.60773320e-01  6.40675416e-01]]
W2-after backprop [[-2.73657334e-01 -1.01815368e+00 -7.96467776e-01  7.32594774e-01
  -6.94174370e-01 -5.97082548e-01 -6.76538909e-02 -1.92188924e-01
   6.72832124e-01 -9.02765146e-01 -2.83134443e-01  9.93986336e-01
   6.01137538e-01  2.59997191e-01  6.89662834e-01 -5.23460183e-01
   1.20747709e+00 -8.53801650e-01 -5.75858908e-01  6.85808656e-01]
 [-7.40012934e-01 -5.32017673e-01 -6.05376035e-01  1.51007712e-01
   4.64623428e-02 -2.68740559e-02 -8.83227007e-01 -8.21156323e-02
   1.58218592e-01  1.15153759e+00 -6.27035035e-01  3.43661033e-01
   1.24477760e+00  5.08372494e-01  1.69294622e-01 -5.89782459e-01
   4.59826046e-01 -4.91599585e-01 -8.66290539e-01 -8.69282588e-01]
 [-1.78508030e-01 -2.66902525e-01 -5.48678443e-01  2.16308868e-01
   4.39216846e-01 -3.48521720e-01  2.71964254e-01 -1.04075412e+00
  -1.43971731e-01 -9.00803454e-01 -1.21448085e+00  1.81499897e-01
   7.68865525e-02  3.23919101e-01  3.43564403e-01 -6.92161508e-01
   8.19877644e-01 -1

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [40]:
# Get vector for word
word = "government"
vec = w2v.word_vec(word)
print(word, vec)

government [-0.98361857  0.38041436 -0.32713566  1.20157159 -0.83414364 -0.69073527
 -0.36241541 -0.66401039 -0.40609313  0.47404528]


In [41]:
# Find similar words
w2v.vec_sim("government", 3)

government 0.9999999999999998
much 0.6503132726102636
the 0.4134225996507453


In [ ]:
#Topic Modelling

In [ ]:
import pandas as pd
pd.set_option("display.max_colwidth", 200)
import numpy as np
import re

In [ ]:
import nltk
from nltk import FreqDist

In [ ]:
import spacy

In [ ]:
import gensim
from gensim import corpora

In [ ]:
import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline

In [ ]:
import pyLDAvis
import pyLDAvis.gensim

In [ ]:
# function to plot most frequent terms
def freq_words(x, terms = 30):
  all_words = ' '.join([text for text in x])
  all_words = all_words.split()

  fdist = FreqDist(all_words)
  words_df = pd.DataFrame({'word':list(fdist.keys()), 'count':list(fdist.values())})

  # selecting top 20 most frequent words
  d = words_df.nlargest(columns="count", n = terms) 
  plt.figure(figsize=(20,5))
  ax = sns.barplot(data=d, x= "word", y = "count")
  ax.set(ylabel = 'Count')
  plt.show()

In [ ]:
freq_words(df['text'])

In [ ]:
# remove unwanted characters, numbers and symbols
df['text'] = df['text'].str.replace("[^a-zA-Z#]", " ")

In [ ]:
from nltk.corpus import stopwords
stop_words = stopwords.words('english')

In [ ]:
# function to remove stopwords
def remove_stopwords(rev):
    rev_new = " ".join([i for i in rev if i not in stop_words])
    return rev_new

# remove short words (length < 3)
df['text'] = df['text'].apply(lambda x: ' '.join([w for w in x.split() if len(w)>2]))

# remove stopwords from the text
wordsText = [remove_stopwords(r.split()) for r in df['text']]

# make entire text lowercase
wordsText = [r.lower() for r in wordsText]

In [ ]:
freq_words(wordsText, 35)

In [ ]:
nlp = spacy.load('en', disable=['parser', 'ner'])

def lemmatization(texts, tags=['NOUN', 'ADJ']): # filter noun and adjective
       output = []
       for sent in texts:
             doc = nlp(" ".join(sent)) 
             output.append([token.lemma_ for token in doc if token.pos_ in tags])
       return output

In [ ]:
tokenized_wordsText = pd.Series(wordsText).apply(lambda x: x.split())
print(tokenized_wordsText[1])

In [ ]:
wordsText_2 = lemmatization(tokenized_wordsText)
print(wordsText_2[1]) # print lemmatized review

In [ ]:
wordsText_3 = []
for i in range(len(wordsText_2)):
    wordsText_3.append(' '.join(wordsText_2[i]))

df['wordsText'] = wordsText_3

freq_words(df['wordsText'], 20)

In [ ]:
dictionary = corpora.Dictionary(wordsText_2)

In [ ]:
doc_term_matrix = [dictionary.doc2bow(rev) for rev in wordsText_2]

In [ ]:
# Creating the object for LDA model using gensim library
LDA = gensim.models.ldamodel.LdaModel

# Build LDA model
lda_model = LDA(corpus=doc_term_matrix, id2word=dictionary, num_topics=7, random_state=100,
                chunksize=1000, passes=50)

In [ ]:
lda_model.print_topics()

In [ ]:
# Visualize the topics
pyLDAvis.enable_notebook()
vis = pyLDAvis.gensim.prepare(lda_model, doc_term_matrix, dictionary)
vis

In [ ]:
#Count vectorization

In [ ]:
from sklearn.feature_extraction.text import CountVectorizer

In [ ]:
from sklearn.feature_extraction.text import CountVectorizer

count_vect = CountVectorizer(analyzer=clean_text)  # call the function clean_text. 
X_counts = count_vect.fit_transform(df['text'])

# X_counts is the vectorized version of the data.

print(X_counts.shape)
#print(count_vect.get_feature_names())  # get_feature_names() prints all the unique words that are found in all of the text messages.

# (3566, 31399) : 3566 text messages, across this 3566 text messages there are 31399 unique words.
# It means the document term matrix consists of 3566 rows and 31399 columns.

# Each row : Text message and the column will have unique words of this text message.

# get_feature_names() : means the numbers are names of the columns. We can remove the numbers and change it to names.






In [ ]:
# Apply CountVectorizer to smaller sample

data_sample = df[0:20]

count_vect_sample = CountVectorizer(analyzer=clean_text)
X_counts_sample = count_vect_sample.fit_transform(data_sample['text'])
print(X_counts_sample.shape)
#print(count_vect_sample.get_feature_names())

# (20, 2951) : 20 rows and 2951 columns.
# There are new feature names. 
# 
# 
print(count_vect_sample)



In [ ]:
# Vectorizers output sparse matrices
#Sparse Matrix: A matrix in which most entries are 0. In the interest of efficient storage, 
#    a sparse matrix will be stored by only storing the locations of the non-zero elements.

X_counts_sample

In [ ]:
X_counts_df = pd.DataFrame(X_counts_sample.toarray())
X_counts_df

# This is the document term Matrix. It has 2951 columns and 20 rows. 
# Values are numbered from 0 to 191 in the columns. 

In [ ]:
X_counts_df.columns = count_vect_sample.get_feature_names()  # Assigning the feature names to the columns
X_counts_df

Bag Of Words Model
Bag-of-words model:
Count how many times does a word occur in each message (Known as term frequency) (TF)
Weigh the counts, so that frequent tokens get lower weight (inverse document frequency)- (IDF)
Normalize the vectors to unit length, to abstract from the original text length (L2 norm)

In [ ]:
# Might take awhile...
train_data = df[0:1000]
bow_transformer = CountVectorizer(analyzer=clean_text).fit(train_data['text'])

# Print total number of vocab words
print(len(bow_transformer.vocabulary_))

In [ ]:
newstest1 = train_data['text'][3]
#print(newstest1)

In [ ]:
bowtest1 = bow_transformer.transform([newstest1])
print(bowtest1)
print(bowtest1.shape)

In [ ]:
news_bows = bow_transformer.transform(train_data['text'])

In [ ]:
print('Shape of Sparse Matrix: ', news_bows.shape)
print('Amount of Non-Zero occurences: ', news_bows.nnz)

In [ ]:
sparsity = (100.0 * news_bows.nnz / (news_bows.shape[0] * news_bows.shape[1]))
print('sparsity: {}'.format(round(sparsity)))

In [ ]:
#TF-IDF

In [ ]:
from sklearn.feature_extraction.text import TfidfTransformer

tfidf_transformer = TfidfTransformer().fit(news_bows)
tfidf4 = tfidf_transformer.transform(bowtest1)
print(tfidf4)

In [ ]:
messages_tfidf = tfidf_transformer.transform(news_bows)
print(messages_tfidf.shape)

In [ ]:
from sklearn.naive_bayes import MultinomialNB
spam_detect_model = MultinomialNB().fit(messages_tfidf, train_data['authors'])

In [ ]:
print('predicted:', spam_detect_model.predict(tfidf4)[0])
print('expected:', train_data.authors[3])

In [ ]:
all_predictions = spam_detect_model.predict(messages_tfidf)
print(all_predictions)

In [ ]:
from sklearn.metrics import classification_report
print (classification_report(train_data['authors'], all_predictions))

In [ ]:
test_data  = df[1001:]

In [ ]:
from sklearn.pipeline import Pipeline

pipeline = Pipeline([
    ('bow', CountVectorizer(analyzer=clean_text)),  # strings to token integer counts
    ('tfidf', TfidfTransformer()),  # integer counts to weighted TF-IDF scores
    ('classifier', MultinomialNB()),  # train on TF-IDF vectors w/ Naive Bayes classifier
])

In [ ]:
#Tensor Flow

In [ ]:
import tensorflow as tf

In [ ]:
var = 0
def countWords(text):
    v = 0
    for i in text:
        v = v + 1
    print(v)
print(var)

In [ ]:
words = []

In [ ]:
# Stemmed vectors are taken as input. 
# Article size: 5 articles are taken.

articles = df.body_text_stemmed.tolist()
for article in articles:
    for word in article:
        words.append(word)
        
len(words)

In [ ]:
# Considering only unique words.
words = set(words)

In [ ]:
vocab_size = len(words) # gives the total number of unique words

In [ ]:
word2int = {}
int2word = {}
for i,word in enumerate(words):
    word2int[word] = i
    int2word[i] = word

In [ ]:
dataTF = []

WINDOW_SIZE = 2

# based on the window size, the neighbouring word or context words is considered for the current word.
# So if the window size is 2, the surrounding words which are at a distance of two words from the current word is processed.

for article in articles[0:5]:
    for word_index, word in enumerate(article):
        for nb_word in article[max(word_index - WINDOW_SIZE, 0) : min(word_index + WINDOW_SIZE, len(article)) + 1] : 
            if nb_word != word:
                dataTF.append([word, nb_word])

In [ ]:
vocab_size = len(words)
vocab_size

In [ ]:
def to_one_hot(data_point_index, vocab_size):
    temp = np.zeros(vocab_size)     # Initializing the temp array with Zeros till the vocab size. like [ 0 0 0]
    temp[data_point_index] = 1    # assigning one value to the data point index. 
    return temp
x_train = [] # input word
y_train = [] # output word

In [ ]:
for data_word in dataTF:
    x_train.append(to_one_hot(word2int[ data_word[0] ], vocab_size))
    y_train.append(to_one_hot(word2int[ data_word[1] ], vocab_size))
# convert them to numpy arrays
x_train = np.asarray(x_train)
y_train = np.asarray(y_train)

In [ ]:
x_train

In [ ]:
print(x_train.shape, y_train.shape)

# meaning 9272 training points, where each point has 1101 dimensions
# or 9272 rows and each row has 1101 columns. 

In [ ]:
# Run this in order to make tensor flow placeholder run on the machine
import tensorflow.compat.v1 as tf
tf.disable_v2_behavior()

In [ ]:
x = tf.placeholder(tf.float32, shape=(None, vocab_size))
y_label = tf.placeholder(tf.float32, shape=(None, vocab_size))

In [ ]:
EMBEDDING_DIM = 5 # you can choose your own number
W1 = tf.Variable(tf.random_normal([vocab_size, EMBEDDING_DIM]))
b1 = tf.Variable(tf.random_normal([EMBEDDING_DIM])) #bias
hidden_representation = tf.add(tf.matmul(x,W1), b1)

In [ ]:
W2 = tf.Variable(tf.random_normal([EMBEDDING_DIM, vocab_size]))
b2 = tf.Variable(tf.random_normal([vocab_size]))
prediction = tf.nn.softmax(tf.add( tf.matmul(hidden_representation, W2), b2))

In [ ]:
# Started at 10.30 AM
sess = tf.Session()
init = tf.global_variables_initializer()
sess.run(init) #make sure you do this!
# define the loss function:
cross_entropy_loss = tf.reduce_mean(-tf.reduce_sum(y_label * tf.log(prediction), reduction_indices=[1]))
# define the training step:
train_step = tf.train.GradientDescentOptimizer(0.1).minimize(cross_entropy_loss)
n_iters = 10000
# train for n_iter iterations
for _ in range(n_iters):
    sess.run(train_step, feed_dict={x: x_train, y_label: y_train})
    print('loss is : ', sess.run(cross_entropy_loss, feed_dict={x: x_train, y_label: y_train}))
# 

In [ ]:
vectors = sess.run(W1 + b1)

In [ ]:
def euclidean_dist(vec1, vec2):
    return np.sqrt(np.sum((vec1-vec2)**2))
def find_closest(word_index, vectors):
    min_dist = 10000 # to act like positive infinity
    min_index = -1
    query_vector = vectors[word_index]
    for index, vector in enumerate(vectors):
        if euclidean_dist(vector, query_vector) < min_dist and not np.array_equal(vector, query_vector):
            min_dist = euclidean_dist(vector, query_vector)
            min_index = index
    return min_index

In [ ]:
# We will now query these vectors with ‘king’, ‘queen’ and ‘royal’
print(int2word[find_closest(word2int['canadian'], vectors)])
print(int2word[find_closest(word2int['pharmaci'], vectors)])
print(int2word[find_closest(word2int['covid19'], vectors)])

In [ ]:
from sklearn.manifold import TSNE
model = TSNE(n_components=2, random_state=0)
np.set_printoptions(suppress=True)
vectors = model.fit_transform(vectors)

In [ ]:
from sklearn.manifold import TSNE
model = TSNE(n_components=2, random_state=0)
np.set_printoptions(suppress=True)
vectors = model.fit_transform(vectors)

In [ ]:
import matplotlib.pyplot as plt
fig, ax = plt.subplots()
for word in words:
    print(word, vectors[word2int[word]][1])
    ax.annotate(word, (vectors[word2int[word]][0],vectors[word2int[word]][1] ))
plt.show()